In [186]:
import numpy as np
import qutip as qt
from scipy.linalg import logm, expm
from qiskit.quantum_info import Operator
from qiskit import QuantumCircuit

from tools.classical import *
from tools.quantum import *

#### Qutip Exact Hamiltonian

In [187]:
num_qubits = 7

X = qt.sigmax()
Y = qt.sigmay()
Z = qt.sigmaz()
hamiltonian_qt = hamiltonian_matrix([X, X], [Y, Y], [Z, Z], coeffs=[1, 1, 1], num_qubits=num_qubits)
# print(hamiltonian_qt)
#* HAMILTONIANS
exact_spec = np.linalg.eigvalsh(hamiltonian_qt)
rescaling_factor, shift = rescaling_and_shift_factors(hamiltonian_qt)  # Shift already rescaled
just_shift = shift * rescaling_factor                                  # Unscaled shift
shifted_hamiltonian_qt = hamiltonian_qt + just_shift * qt.qeye(hamiltonian_qt.shape[0])
rescaled_hamiltonian_qt = hamiltonian_qt / rescaling_factor + shift * qt.qeye(hamiltonian_qt.shape[0])

#* SPECTRUMS
# print(f'Shifted spectrum {np.linalg.eigvalsh(shifted_hamiltonian_qt)}')
print(f'Rescaling factor {rescaling_factor}')
print(f'Shift {shift}')
print(f'Original spectrum {exact_spec}')
print(f'Normalized spectrum {np.linalg.eigvalsh(rescaled_hamiltonian_qt)}')

Rescaling factor 18.42072
Shift 0.6199931381618091
Original spectrum [-11.42071703 -11.42071703 -11.42071703 -11.42071703  -7.22510153
  -7.22510153  -7.22510153  -7.22510153  -7.22510153  -7.22510153
  -7.22510153  -7.22510153  -7.07672523  -7.07672523  -7.07672523
  -7.07672523  -5.          -5.          -5.          -5.
  -4.44762362  -4.44762362  -4.44762362  -4.44762362  -3.28929176
  -3.28929176  -3.28929176  -3.28929176  -3.28929176  -3.28929176
  -3.28929176  -3.28929176  -3.          -3.          -3.
  -3.          -2.48229397  -2.48229397  -2.48229397  -2.48229397
  -2.48229397  -2.48229397  -2.48229397  -2.48229397  -0.87273315
  -0.87273315  -0.87273315  -0.87273315  -0.87273315  -0.87273315
  -0.87273315  -0.87273315  -0.67711765  -0.67711765  -0.67711765
  -0.67711765  -0.60387547  -0.60387547  -0.60387547  -0.60387547
  -0.60387547  -0.60387547  -0.60387547  -0.60387547  -0.60387547
  -0.60387547  -0.60387547  -0.60387547   1.16141536   1.16141536
   1.16141536   1.16141

### Qutip unitary evolution construction and comparison: Exact vs Trotterized

In [188]:
T = 1
total_time = T * 2 * np.pi
rescaled_time = total_time / rescaling_factor
num_trotter_steps = 1000

step_size = total_time / num_trotter_steps
rescaled_step_size = rescaled_time / num_trotter_steps

#* EXACT UNITARIES
exact_U_qt = expm(1j * hamiltonian_qt * total_time)
shifted_exact_U_qt = expm(1j * shifted_hamiltonian_qt * total_time) 
normalized_exact_U_qt = expm(1j * hamiltonian_qt * rescaled_time + 1j * shift * total_time * qt.qeye(hamiltonian_qt.shape[0]))

#* QUTIP TROTTER
trott_U_qt = trotter_heisenberg_qutip(num_qubits, step_size, num_trotter_steps)
shifted_trott_U_qt = trotter_heisenberg_qutip(num_qubits, step_size, num_trotter_steps, shift=(total_time*just_shift))
normalized_trott_U_qt = trotter_heisenberg_qutip(num_qubits, rescaled_step_size, num_trotter_steps, shift=(total_time*shift))
# UUdag_minus_id = exact_U_qt * trott_U_qt.dag() - qt.qeye(exact_U_qt.shape[0])

#* QUTIP DISTANCES
dist_between_unitaries = np.linalg.norm(exact_U_qt - trott_U_qt)
dist_between_shifted_unitaries = np.linalg.norm(shifted_exact_U_qt - shifted_trott_U_qt)
dist_between_normalized_unitaries = np.linalg.norm(normalized_exact_U_qt - normalized_trott_U_qt)
print(f'Distance between Qutip Trotter vs Exact {dist_between_unitaries}')
print(f'Distance between Shifted Qutip Trotter vs Exact {dist_between_shifted_unitaries}')
print(f'Distance between Normalized Qutip Trotter vs Exact {dist_between_normalized_unitaries}')
# with np.printoptions(precision=3, suppress=True):
#     print(exact_U_qt)
#     print(trott_U_qt)
#     print(UUdag_minus_id)
    
# logU_shifted = logm(shifted_trott_U_qt) / (1j * T)
# logU = logm(trott_U_qt) / (1j * T)
# dist_shifted = np.linalg.norm(logU_shifted - shifted_exact_U_qt)
# dist = np.linalg.norm(logU - exact_U_qt)
# print(dist_shifted)
# print(dist)

Distance between Qutip Trotter vs Exact 2.064044211037568
Distance between Shifted Qutip Trotter vs Exact 2.06404421103757
Distance between Normalized Qutip Trotter vs Exact 0.007906457317136944


### Observable expectation comparison: Exact vs Trotterized, finding a good number of Trotter steps

In [189]:
#* Initial state
# initial_state = np.ones(2**num_qubits) / np.sqrt(2**num_qubits)  # Equal superposition
# np.random.seed(667)
rand_ini_state = np.random.random(2**num_qubits) + 1j * np.random.random(2**num_qubits)  # Random state
rand_ini_state /= np.linalg.norm(rand_ini_state)
initial_energy = qt.expect(qt.Qobj(hamiltonian_qt), qt.Qobj(rand_ini_state))
print(f'Initial energy {initial_energy}')

#TODO: Use some zeros in the entries
randstate_better = np.zeros(2**num_qubits)
randstate_better[np.random.choice(2**num_qubits, 2**num_qubits//4, replace=False)] = 1
randstate_better /= np.linalg.norm(randstate_better)
rand_state0 = np.random.random(2**num_qubits) + 1j * np.random.random(2**num_qubits)  # Random state
rand_state0 /= np.linalg.norm(rand_state0)
rand_state1 = np.random.random(2**num_qubits) + 1j * np.random.random(2**num_qubits)  # Random state
rand_state1 /= np.linalg.norm(rand_state1)

rand_ini_state = randstate_better
print(qt.fidelity(qt.Qobj(randstate_better), qt.Qobj(rand_state1)))

#* Evolved states
exact_evolved_state = qt.Qobj(exact_U_qt) * qt.Qobj(rand_ini_state)
trott_evolved_state = qt.Qobj(trott_U_qt) * qt.Qobj(rand_ini_state)

exact_evolved_state_shifted = qt.Qobj(shifted_exact_U_qt) * qt.Qobj(rand_ini_state)
trott_evolved_state_shifted = qt.Qobj(shifted_trott_U_qt) * qt.Qobj(rand_ini_state)

exact_evolved_state_normalized = qt.Qobj(normalized_exact_U_qt) * qt.Qobj(rand_ini_state)
trott_evolved_state_normalized = qt.Qobj(normalized_trott_U_qt) * qt.Qobj(rand_ini_state)

#* Fidelities
exact_evolved_fidelity = qt.fidelity(exact_evolved_state, trott_evolved_state)
exact_evolved_fidelity_normalized = qt.fidelity(exact_evolved_state_normalized, trott_evolved_state_normalized)
# print('Shifted:')  #* Global phase won't show up in fidelity
# fid_of_states_shifted = qt.fidelity(exact_evolved_state_shifted, trott_evolved_state_shifted)
print(f'Exact-Evolved fidelity {exact_evolved_fidelity}')
print(f'Rescaled + shifted exact-evolved fidelity {exact_evolved_fidelity_normalized}')


Initial energy 5.562324371919299
0.43666496009911243
Exact-Evolved fidelity 0.9877285540956716
Rescaled + shifted exact-evolved fidelity 0.9999998322421659


#### Circuit

In [190]:
trotter_step = trotter_step_heisenberg(num_qubits)
ham_time_evol = lambda m, T, sh: ham_evol(num_qubits, trotter_step=trotter_step, num_trotter_steps=m, time=T,
                                          shift = sh)

# num_trott_steps = int(np.ceil(8 * np.pi * np.abs(T) / rescaling_factor))

time_evol_circ = ham_time_evol(num_trotter_steps, total_time, 0)
time_evol_circ_shifted = ham_time_evol(num_trotter_steps, total_time, total_time*just_shift)
time_evol_circ_normalized = ham_time_evol(num_trotter_steps, rescaled_time, total_time*shift)

circ = QuantumCircuit(num_qubits, name="H")
circ_shifted = QuantumCircuit(num_qubits, name="H")
circ_normalized = QuantumCircuit(num_qubits, name="H")

circ.compose(time_evol_circ, range(num_qubits), inplace=True)
circ_shifted.compose(time_evol_circ_shifted, range(num_qubits), inplace=True)
circ_normalized.compose(time_evol_circ_normalized, range(num_qubits), inplace=True)

print(f'#Qubits {num_qubits}')
print(f'#Trotter steps {num_trotter_steps}')
print(f'#Gates {len([(op, _, _) for (op, _, _) in circ.data])}')
# print(circ)
# print(circ_shifted)
print(circ_normalized)


#Qubits 7
#Trotter steps 1000
#Gates 21000
global phase: 3.8955
     ┌───────────────────┐┌───────────────────┐                  »
q_0: ┤0                  ├┤0                  ├─■────────────────»
     │  Rxx(-0.00068219) ││  Ryy(-0.00068219) │ │ZZ(-0.00068219) »
q_1: ┤1                  ├┤1                  ├─■────────────────»
     └───────────────────┘└───────────────────┘                  »
q_2: ────────────────────────────────────────────────────────────»
                                                                 »
q_3: ────────────────────────────────────────────────────────────»
                                                                 »
q_4: ────────────────────────────────────────────────────────────»
                                                                 »
q_5: ────────────────────────────────────────────────────────────»
                                                                 »
q_6: ────────────────────────────────────────────────────────────

### Comparing Circuit unitary operator to Exact

In [191]:
#* Circuit operators
trotterized_evolution_unitary = Operator(circ).data
trotterized_evolution_unitary_shifted = Operator(circ_shifted).data
trotterized_evolution_unitary_normalized = Operator(circ_normalized).data

#* Distance to exact unitary
dist_circ_unitary_vs_exact = np.linalg.norm(trotterized_evolution_unitary - exact_U_qt)
dist_circ_unitary_vs_exact_shifted = np.linalg.norm(trotterized_evolution_unitary_shifted - shifted_exact_U_qt)
dist_circ_unitary_vs_exact_normalized = np.linalg.norm(trotterized_evolution_unitary_normalized - normalized_exact_U_qt)

print(f'Distance between circ unitary and exact {dist_circ_unitary_vs_exact}')
print(f'Distance between circ unitary and exact shifted {dist_circ_unitary_vs_exact_shifted}')
print(f'Distance between circ unitary and exact normalized {dist_circ_unitary_vs_exact_normalized}')

Distance between circ unitary and exact 2.0640442110370785
Distance between circ unitary and exact shifted 2.064044211037076
Distance between circ unitary and exact normalized 0.007906457334283983


### Fidelity of Circuit vs Exact

In [192]:
circ_with_ini_state = QuantumCircuit(num_qubits, name="H")
circ_with_ini_state_normalized = QuantumCircuit(num_qubits, name="H")

circ_with_ini_state.initialize(rand_ini_state, range(num_qubits))
circ_with_ini_state_normalized.initialize(rand_ini_state, range(num_qubits))

circ_with_ini_state.compose(time_evol_circ, range(num_qubits), inplace=True)
circ_with_ini_state_normalized.compose(time_evol_circ_normalized, range(num_qubits), inplace=True)

qiskit_end_state = qt.Qobj(Statevector(circ_with_ini_state).data)  # Circ to state
qiskit_end_state_normalized = qt.Qobj(Statevector(circ_with_ini_state_normalized).data)
# qiskit_end_state_2 = qt.Qobj(trotterized_evolution_unitary) * qt.Qobj(rand_ini_state)  # Circ to op, op * ini_state


#TODO: Check Qiskit vs Qutip convention for up - down, i.e. MSB - LSB
#TODO: 1 more or less Trotter steps than Qutip
print('EXACT')
print(f'Fidelity Trotters {qt.fidelity(trott_evolved_state, qiskit_end_state)}')
print(f'Fidelity Qutip Trotter vs Exact {qt.fidelity(trott_evolved_state, exact_evolved_state)}')
print(f'Fidelity Qiskit Trotter vs Exact {qt.fidelity(qiskit_end_state, exact_evolved_state)}')

print('NORMALIZED')
print(f'Fidelity Trotters {qt.fidelity(trott_evolved_state_normalized, qiskit_end_state_normalized)}')
print(f'Fidelity Qutip Trotter vs Exact {qt.fidelity(trott_evolved_state_normalized, exact_evolved_state_normalized)}')
print(f'Fidelity Qiskit Trotter vs Exact {qt.fidelity(qiskit_end_state_normalized, exact_evolved_state_normalized)}')

EXACT
Fidelity Trotters 0.9999354432411804
Fidelity Qutip Trotter vs Exact 0.9877285540956716
Fidelity Qiskit Trotter vs Exact 0.9878374481297876
NORMALIZED
Fidelity Trotters 0.9999998406413613
Fidelity Qutip Trotter vs Exact 0.9999998322421659
Fidelity Qiskit Trotter vs Exact 0.9999998208686878


### Trotterized Hamiltonian comparison, Qiskit vs Exact, Qutip vs Exact

In [193]:
#* LOGM
# logU = logm(trotterized_evolution_unitary)  # log U = i 2pi H T / rescaling_factor  #! It's not unique if any eigenenergy < 0
# trotterized_ham_from_circuit = logU / (1j * T) #- shift * qt.qeye(hamiltonian_qt.shape[0])
# qiskit_trott_ham_spec = np.linalg.eigvalsh(trotterized_ham_from_circuit)
# spectrum_dist = np.linalg.norm(qiskit_trott_ham_spec - exact_spec)
# print(f'Spectrum distance {spectrum_dist}')

#### Qiskit gate angle convention! RXX(-2x) = exp(x)

In [194]:
c = QuantumCircuit(2)
c.rxx(np.pi/2, 0, 1)
op = Operator(c)
print(op.data)
X = qt.sigmax()
XX = qt.tensor(X, X)
op_qt = expm(-1j*np.pi* XX / 4)
print(op_qt)


[[0.70710678+0.j         0.        +0.j         0.        +0.j
  0.        -0.70710678j]
 [0.        +0.j         0.70710678+0.j         0.        -0.70710678j
  0.        +0.j        ]
 [0.        +0.j         0.        -0.70710678j 0.70710678+0.j
  0.        +0.j        ]
 [0.        -0.70710678j 0.        +0.j         0.        +0.j
  0.70710678+0.j        ]]
[[0.70710678+0.j         0.        +0.j         0.        +0.j
  0.        -0.70710678j]
 [0.        +0.j         0.70710678+0.j         0.        -0.70710678j
  0.        +0.j        ]
 [0.        +0.j         0.        -0.70710678j 0.70710678+0.j
  0.        +0.j        ]
 [0.        -0.70710678j 0.        +0.j         0.        +0.j
  0.70710678+0.j        ]]
